## Train test validation split

In [35]:
import pandas as pd
import numpy as np

from gensim.models import Word2Vec

from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer

from sklearn.cluster import KMeans
from sklearn.naive_bayes import MultinomialNB
from sklearn.linear_model import LogisticRegression
from sklearn.svm import LinearSVC
from sklearn.linear_model import SGDClassifier

from sklearn import metrics
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_val_score

In [2]:
df = pd.read_csv('data_speech_all.csv', sep='\t', encoding='utf-8')
X  = df['segmented']
y  = df['intent']

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=0)
X_test_test, X_test_valid, y_test_test, y_test_valid = train_test_split(X_test, y_test, test_size=0.5, random_state=1)


# BOW without features
### BOW + naive bayes

In [3]:
stop_ch = ['的', '了', '和', '而', '且', '1','2','3','4','5','6','7','8','9','10','11','12','一个','一','二','三','四','五','六','七','八','九','十','十一','十二']


In [4]:
count_vect          = CountVectorizer(stop_words=stop_ch, ngram_range=(1,2))
X_train_counts      = count_vect.fit_transform(X_train)

clf_NB_counts       = MultinomialNB()
model_NB_counts     = clf_NB_counts.fit(X_train_counts, y_train)
predicted_NB_counts = model_NB_counts.predict(count_vect.transform(X_test_test))
print(metrics.accuracy_score(y_test_test, predicted_NB_counts))
print(clf_NB_counts.predict(count_vect.transform(["我 觉得 五七 里面 肯定 有 一匹 狼"]))) # "I think in 5 and 7 there must be a wolf"

0.400843881857
['attack']


### Tf-idf + naive bayes

In [5]:
tfidf_vect          = TfidfVectorizer(min_df=.0025, max_df=.1, max_features=100000,stop_words=stop_ch,token_pattern='[\u4e00-\u9fff]+',analyzer='word', ngram_range=(1,2),use_idf=True)
X_train_tfidf       = tfidf_vect.fit_transform(X_train)

clf_NB_tfidf       = MultinomialNB()
model_NB_tfidf     = clf_NB_tfidf.fit(X_train_tfidf, y_train)
predicted_NB_tfidf = model_NB_tfidf.predict(tfidf_vect.transform(X_test_test))
print(metrics.accuracy_score(y_test_test, predicted_NB_tfidf))
print(clf_NB_tfidf.predict(tfidf_vect.transform(["我 觉得 五七 里面 肯定 有 一匹 狼"]))) 

0.449367088608
['attack']


#### choose hyper parameters with gridsearch and pipeline

In [12]:
stop_ch1 = ['的', '了', '和', '而', '且', '1','2','3','4','5','6','7','8','9','10','11','12','一个','一','二','三','四','五','六','七','八','九','十','十一','十二']
stop_ch2 = ['的', '了', '和', '而', '且']

pipeline = Pipeline([
    ('tfidf', TfidfVectorizer(token_pattern='[\u4e00-\u9fff]+',analyzer='word',use_idf=True)),
    ('clf', MultinomialNB(fit_prior=True, class_prior=None))
])
parameters = {
    'tfidf__max_df': (0.1, 0.25, 0.5, 0.75),
    'tfidf__min_df': (0.001, 0.0025, 0.005, 0.025),
    'tfidf__max_features': (None, 5000, 10000, 50000, 100000),
    'tfidf__norm': ('l1','l2',),
    'tfidf__stop_words': (stop_ch1,stop_ch2),
    'tfidf__ngram_range': ((1, 1), (1, 2),(1,3)),
    'clf__alpha': (1e-2, 1e-3)
}

grid_search_tune = GridSearchCV(pipeline, parameters, cv=5, n_jobs=5, verbose=2)
grid_search_tune.fit(X_test_valid, y_test_valid)

print("Best parameters set:")
print(grid_search_tune.best_estimator_.steps)
print(grid_search_tune.best_score_)

Fitting 5 folds for each of 1920 candidates, totalling 9600 fits
[CV] clf__alpha=0.01, tfidf__max_df=0.1, tfidf__max_features=None, tfidf__min_df=0.001, tfidf__ngram_range=(1, 1), tfidf__norm=l1, tfidf__stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'] 
[CV] clf__alpha=0.01, tfidf__max_df=0.1, tfidf__max_features=None, tfidf__min_df=0.001, tfidf__ngram_range=(1, 1), tfidf__norm=l1, tfidf__stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'] 
[CV] clf__alpha=0.01, tfidf__max_df=0.1, tfidf__max_features=None, tfidf__min_df=0.001, tfidf__ngram_range=(1, 1), tfidf__norm=l1, tfidf__stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'] 
[CV] clf__alph

[CV] clf__alpha=0.01, tfidf__max_df=0.1, tfidf__max_features=None, tfidf__min_df=0.001, tfidf__ngram_range=(1, 1), tfidf__norm=l2, tfidf__stop_words=['的', '了', '和', '而', '且'] 
[CV]  clf__alpha=0.01, tfidf__max_df=0.1, tfidf__max_features=None, tfidf__min_df=0.001, tfidf__ngram_range=(1, 1), tfidf__norm=l2, tfidf__stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'], total=   0.1s
[CV]  clf__alpha=0.01, tfidf__max_df=0.1, tfidf__max_features=None, tfidf__min_df=0.001, tfidf__ngram_range=(1, 1), tfidf__norm=l2, tfidf__stop_words=['的', '了', '和', '而', '且'], total=   0.1s
[CV] clf__alpha=0.01, tfidf__max_df=0.1, tfidf__max_features=None, tfidf__min_df=0.001, tfidf__ngram_range=(1, 2), tfidf__norm=l1, tfidf__stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'] 
[CV]

[CV] clf__alpha=0.01, tfidf__max_df=0.1, tfidf__max_features=None, tfidf__min_df=0.001, tfidf__ngram_range=(1, 2), tfidf__norm=l2, tfidf__stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'] 
[CV]  clf__alpha=0.01, tfidf__max_df=0.1, tfidf__max_features=None, tfidf__min_df=0.001, tfidf__ngram_range=(1, 2), tfidf__norm=l2, tfidf__stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'], total=   0.2s
[CV] clf__alpha=0.01, tfidf__max_df=0.1, tfidf__max_features=None, tfidf__min_df=0.001, tfidf__ngram_range=(1, 2), tfidf__norm=l2, tfidf__stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'] 
[CV]  clf__alpha=0.01, tfidf__max_df=0.1, tfidf__max_features=No

[CV]  clf__alpha=0.01, tfidf__max_df=0.1, tfidf__max_features=None, tfidf__min_df=0.001, tfidf__ngram_range=(1, 3), tfidf__norm=l1, tfidf__stop_words=['的', '了', '和', '而', '且'], total=   0.2s
[CV] clf__alpha=0.01, tfidf__max_df=0.1, tfidf__max_features=None, tfidf__min_df=0.001, tfidf__ngram_range=(1, 3), tfidf__norm=l2, tfidf__stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'] 
[CV]  clf__alpha=0.01, tfidf__max_df=0.1, tfidf__max_features=None, tfidf__min_df=0.001, tfidf__ngram_range=(1, 3), tfidf__norm=l1, tfidf__stop_words=['的', '了', '和', '而', '且'], total=   0.3s
[CV] clf__alpha=0.01, tfidf__max_df=0.1, tfidf__max_features=None, tfidf__min_df=0.001, tfidf__ngram_range=(1, 3), tfidf__norm=l2, tfidf__stop_words=['的', '了', '和', '而', '且'] 
[CV]  clf__alpha=0.01, tfidf__max_df=0.1, tfidf__max_features=None, tfidf__min_df=0.001, tfidf__ngram_range=(1, 3), tfidf__norm=l1, tfi

[Parallel(n_jobs=5)]: Done  52 tasks      | elapsed:    3.3s


...

[CV]  clf__alpha=0.001, tfidf__max_df=0.75, tfidf__max_features=100000, tfidf__min_df=0.025, tfidf__ngram_range=(1, 1), tfidf__norm=l2, tfidf__stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'], total=   0.1s
[CV]  clf__alpha=0.001, tfidf__max_df=0.75, tfidf__max_features=100000, tfidf__min_df=0.005, tfidf__ngram_range=(1, 3), tfidf__norm=l2, tfidf__stop_words=['的', '了', '和', '而', '且'], total=   0.8s
[CV]  clf__alpha=0.001, tfidf__max_df=0.75, tfidf__max_features=100000, tfidf__min_df=0.025, tfidf__ngram_range=(1, 1), tfidf__norm=l2, tfidf__stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'], total=   0.1s
[CV]  clf__alpha=0.001, tfidf__max_df=0.75, tfidf__max_features=100000, tfidf__min_df=0.025, tfidf__ngram_range=(1, 1), tfidf__norm=l2, tfidf__stop_words

[CV] clf__alpha=0.001, tfidf__max_df=0.75, tfidf__max_features=100000, tfidf__min_df=0.025, tfidf__ngram_range=(1, 2), tfidf__norm=l2, tfidf__stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'] 
[CV]  clf__alpha=0.001, tfidf__max_df=0.75, tfidf__max_features=100000, tfidf__min_df=0.025, tfidf__ngram_range=(1, 2), tfidf__norm=l1, tfidf__stop_words=['的', '了', '和', '而', '且'], total=   0.2s
[CV] clf__alpha=0.001, tfidf__max_df=0.75, tfidf__max_features=100000, tfidf__min_df=0.025, tfidf__ngram_range=(1, 2), tfidf__norm=l2, tfidf__stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'] 
[CV]  clf__alpha=0.001, tfidf__max_df=0.75, tfidf__max_features=100000, tfidf__min_df=0.025, tfidf__ngram_range=(1, 2), tfidf__norm=l1, tfidf__stop_words=['的', '了', '和', '而', '且'], to

[CV] clf__alpha=0.001, tfidf__max_df=0.75, tfidf__max_features=100000, tfidf__min_df=0.025, tfidf__ngram_range=(1, 3), tfidf__norm=l1, tfidf__stop_words=['的', '了', '和', '而', '且'] 
[CV]  clf__alpha=0.001, tfidf__max_df=0.75, tfidf__max_features=100000, tfidf__min_df=0.025, tfidf__ngram_range=(1, 3), tfidf__norm=l1, tfidf__stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'], total=   0.4s
[CV] clf__alpha=0.001, tfidf__max_df=0.75, tfidf__max_features=100000, tfidf__min_df=0.025, tfidf__ngram_range=(1, 3), tfidf__norm=l1, tfidf__stop_words=['的', '了', '和', '而', '且'] 
[CV]  clf__alpha=0.001, tfidf__max_df=0.75, tfidf__max_features=100000, tfidf__min_df=0.025, tfidf__ngram_range=(1, 3), tfidf__norm=l1, tfidf__stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'], to

[Parallel(n_jobs=5)]: Done 9600 out of 9600 | elapsed: 10.8min finished


Best parameters set:
[('tfidf', TfidfVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.25, max_features=None, min_df=0.005,
        ngram_range=(1, 2), norm='l2', preprocessor=None, smooth_idf=True,
        stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'],
        strip_accents=None, sublinear_tf=False,
        token_pattern='[一-\u9fff]+', tokenizer=None, use_idf=True,
        vocabulary=None)), ('clf', MultinomialNB(alpha=0.01, class_prior=None, fit_prior=True))]
0.446315789474


#### result:
Best parameters set (on validation set, cv=5):
[('tfidf', TfidfVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, **max_df=0.25**, max_features=None, min_df=0.005,
        **ngram_range=(1, 2)**, norm='l2', preprocessor=None, smooth_idf=True,
        stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'],
        strip_accents=None, sublinear_tf=False,
        token_pattern='[一-\u9fff]+', tokenizer=None, use_idf=True,
        vocabulary=None)), ('clf', MultinomialNB(alpha=0.01, class_prior=None, fit_prior=True))]
0.446315789474

Best parameters set (on train set, cv=2):
[('tfidf', TfidfVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, **max_df=0.75**, max_features=None, min_df=0.005,
        **ngram_range=(1, 3)**, norm='l2', preprocessor=None, smooth_idf=True,
        stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'],
        strip_accents=None, sublinear_tf=False,
        token_pattern='[一-\u9fff]+', tokenizer=None, use_idf=True,
        vocabulary=None)), ('clf', MultinomialNB(alpha=0.01, class_prior=None, fit_prior=True))]
0.48063188608

### Tf-idf + Multinomial LogisticRegression

In [11]:
# tfidf hparams are the optimal by the last grid search
tfidf_vect          = TfidfVectorizer(min_df=.005, max_df=0.75, max_features=None,stop_words=stop_ch1,token_pattern='[\u4e00-\u9fff]+',analyzer='word', ngram_range=(1, 3), norm='l2',use_idf=True)
X_train_tfidf       = tfidf_vect.fit_transform(X_train)


clf_LR_tfidf = LogisticRegression(solver='newton-cg',multi_class='multinomial')
model_LR_tfidf = clf_LR_tfidf.fit(X_train_tfidf, y_train)
predicted_LR_tfidf = model_LR_tfidf.predict(tfidf_vect.transform(X_test_test))
print(metrics.accuracy_score(y_test_test, predicted_LR_tfidf))
print(clf_LR_tfidf.predict(tfidf_vect.transform(["我 觉得 五七 里面 肯定 有 一匹 狼"]))) 

0.493670886076
['attack']


#### grid search for classifier (keep the tfidf vectorizer as the optimal hpramas)

In [14]:
pipeline = Pipeline([
    ('tfidf', TfidfVectorizer(token_pattern='[\u4e00-\u9fff]+',analyzer='word',use_idf=True,norm='l2',min_df=0.005, max_features=None,stop_words=stop_ch1)),
    ('clf', LogisticRegression(multi_class='multinomial'))
])
parameters = {
    'tfidf__max_df': (0.25, 0.5, 0.75),
    'tfidf__ngram_range': ((1, 1), (1, 2),(1,3)),
    'clf__C': [0.001, 0.01, 0.1, 1, 10, 100, 1000],
    'clf__solver': ('newton-cg','lbfgs','sag','saga')
}

grid_search_tune = GridSearchCV(pipeline, parameters, cv=5, n_jobs=5, verbose=2)
grid_search_tune.fit(X_test_valid, y_test_valid)

print("Best parameters set:")
print(grid_search_tune.best_estimator_.steps)
print(grid_search_tune.best_score_)

Fitting 2 folds for each of 252 candidates, totalling 504 fits
[CV] clf__C=0.001, clf__solver=newton-cg, tfidf__max_df=0.25, tfidf__ngram_range=(1, 1) 
[CV] clf__C=0.001, clf__solver=newton-cg, tfidf__max_df=0.25, tfidf__ngram_range=(1, 1) 
[CV]  clf__C=0.001, clf__solver=newton-cg, tfidf__max_df=0.25, tfidf__ngram_range=(1, 1), total=   0.1s
[CV] clf__C=0.001, clf__solver=newton-cg, tfidf__max_df=0.25, tfidf__ngram_range=(1, 2) 
[CV]  clf__C=0.001, clf__solver=newton-cg, tfidf__max_df=0.25, tfidf__ngram_range=(1, 1), total=   0.1s
[CV] clf__C=0.001, clf__solver=newton-cg, tfidf__max_df=0.25, tfidf__ngram_range=(1, 2) 
[CV]  clf__C=0.001, clf__solver=newton-cg, tfidf__max_df=0.25, tfidf__ngram_range=(1, 2), total=   0.1s
[CV] clf__C=0.001, clf__solver=newton-cg, tfidf__max_df=0.25, tfidf__ngram_range=(1, 3) 
[CV]  clf__C=0.001, clf__solver=newton-cg, tfidf__max_df=0.25, tfidf__ngram_range=(1, 2), total=   0.1s
[CV] clf__C=0.001, clf__solver=newton-cg, tfidf__max_df=0.5, tfidf__ngram_ra

/Users/manyingz/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)


[CV]  clf__C=0.001, clf__solver=sag, tfidf__max_df=0.25, tfidf__ngram_range=(1, 1), total=   0.2s
[CV] clf__C=0.001, clf__solver=sag, tfidf__max_df=0.25, tfidf__ngram_range=(1, 1) 


/Users/manyingz/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)


[CV]  clf__C=0.001, clf__solver=sag, tfidf__max_df=0.25, tfidf__ngram_range=(1, 1), total=   0.2s
[CV] clf__C=0.001, clf__solver=sag, tfidf__max_df=0.25, tfidf__ngram_range=(1, 2) 
[CV]  clf__C=0.001, clf__solver=lbfgs, tfidf__max_df=0.75, tfidf__ngram_range=(1, 3), total=   0.3s
[CV] clf__C=0.001, clf__solver=sag, tfidf__max_df=0.25, tfidf__ngram_range=(1, 3) 


...

/Users/manyingz/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)


[CV]  clf__C=1000, clf__solver=saga, tfidf__max_df=0.75, tfidf__ngram_range=(1, 3), total=   0.2s


[Parallel(n_jobs=2)]: Done 504 out of 504 | elapsed:   55.1s finished


Best parameters set:
[('tfidf', TfidfVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_features=None, min_df=0.005,
        ngram_range=(1, 2), norm='l2', preprocessor=None, smooth_idf=True,
        stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'],
        strip_accents=None, sublinear_tf=False,
        token_pattern='[一-\u9fff]+', tokenizer=None, use_idf=True,
        vocabulary=None)), ('clf', LogisticRegression(C=10, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='multinomial',
          n_jobs=1, penalty='l2', random_state=None, solver='saga',
          tol=0.0001, verbose=0, warm_start=False))]
0.442105263158


/Users/manyingz/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)


#### result

Best parameters set (on validation set, cv=5):
[('tfidf', TfidfVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_features=None, min_df=0.005,
        **ngram_range=(1, 1)**, norm='l2', preprocessor=None, smooth_idf=True,
        stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'],
        strip_accents=None, sublinear_tf=False,
        token_pattern='[一-\u9fff]+', tokenizer=None, use_idf=True,
        vocabulary=None)), ('clf', LogisticRegression(C=10, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='multinomial',
          n_jobs=1, penalty='l2', random_state=None, solver='saga',
          tol=0.0001, verbose=0, warm_start=False))]
0.458947368421

Best parameters set (on validation set, cv=2):
[('tfidf', TfidfVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_features=None, min_df=0.005,
        **ngram_range=(1, 2)**, norm='l2', preprocessor=None, smooth_idf=True,
        stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'],
        strip_accents=None, sublinear_tf=False,
        token_pattern='[一-\u9fff]+', tokenizer=None, use_idf=True,
        vocabulary=None)), ('clf', LogisticRegression(C=10, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='multinomial',
          n_jobs=1, penalty='l2', random_state=None, solver='saga',
          tol=0.0001, verbose=0, warm_start=False))]
0.442105263158

#### fine-tune C in LR

In [24]:
pipeline = Pipeline([
    ('tfidf', TfidfVectorizer(token_pattern='[\u4e00-\u9fff]+',ngram_range=(1, 2),max_df=0.75,analyzer='word',use_idf=True,norm='l2',min_df=0.005, max_features=None,stop_words=stop_ch1)),
    ('clf', LogisticRegression(multi_class='multinomial',solver='saga'))
])
parameters = {
    'clf__C': [4.61,4.62,4.63,4.64,4.65,4.66,4.67,4.68,4.69,4.7,4.71,4.72,4.73,4.74,4.75,4.76,4.77,4.78,4.79]
}

grid_search_tune = GridSearchCV(pipeline, parameters, cv=5, n_jobs=5, verbose=2)
grid_search_tune.fit(X_test_valid, y_test_valid)

print("Best parameters set:")
print(grid_search_tune.best_estimator_.steps)
print(grid_search_tune.best_score_)

Fitting 5 folds for each of 19 candidates, totalling 95 fits
[CV] clf__C=4.61 .....................................................
[CV] clf__C=4.61 .....................................................
[CV] clf__C=4.61 .....................................................
[CV] clf__C=4.61 .....................................................
[CV] clf__C=4.61 .....................................................


/Users/manyingz/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/Users/manyingz/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/Users/manyingz/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/Users/manyingz/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/Users/manyingz/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: T

[CV] ...................................... clf__C=4.61, total=   0.4s
[CV] clf__C=4.62 .....................................................
[CV] ...................................... clf__C=4.61, total=   0.4s
[CV] clf__C=4.62 .....................................................
[CV] ...................................... clf__C=4.61, total=   0.4s
[CV] clf__C=4.62 .....................................................
[CV] ...................................... clf__C=4.61, total=   0.4s
[CV] clf__C=4.62 .....................................................
[CV] ...................................... clf__C=4.61, total=   0.4s
[CV] clf__C=4.62 .....................................................


/Users/manyingz/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/Users/manyingz/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/Users/manyingz/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/Users/manyingz/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/Users/manyingz/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: T

[CV] ...................................... clf__C=4.62, total=   0.4s
[CV] clf__C=4.63 .....................................................
[CV] ...................................... clf__C=4.62, total=   0.4s
[CV] ...................................... clf__C=4.62, total=   0.4s
[CV] clf__C=4.63 .....................................................
[CV] clf__C=4.63 .....................................................
[CV] ...................................... clf__C=4.62, total=   0.4s
[CV] clf__C=4.63 .....................................................
[CV] ...................................... clf__C=4.62, total=   0.4s
[CV] clf__C=4.63 .....................................................


...

/Users/manyingz/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/Users/manyingz/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/Users/manyingz/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/Users/manyingz/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)


[CV] ...................................... clf__C=4.79, total=   0.4s
[CV] ...................................... clf__C=4.79, total=   0.4s
[CV] ...................................... clf__C=4.79, total=   0.4s


/Users/manyingz/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)


[CV] ...................................... clf__C=4.79, total=   0.4s
[CV] ...................................... clf__C=4.79, total=   0.4s
Best parameters set:
[('tfidf', TfidfVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_features=None, min_df=0.005,
        ngram_range=(1, 2), norm='l2', preprocessor=None, smooth_idf=True,
        stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'],
        strip_accents=None, sublinear_tf=False,
        token_pattern='[一-\u9fff]+', tokenizer=None, use_idf=True,
        vocabulary=None)), ('clf', LogisticRegression(C=4.64, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='multinomial',
          n_jobs=1, penalty='l2', random_state=None, solver='s

[Parallel(n_jobs=5)]: Done  95 out of  95 | elapsed:   10.3s finished
/Users/manyingz/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)


C=4, 0.461052631579

C=4.7, 0.467368421053

C=4.64, 0.467368421053

### Tf-idf + SVM

In [26]:
clf_SVM_tfidf = LinearSVC()
model_SVM_tfidf = clf_SVM_tfidf.fit(X_train_tfidf, y_train)
predicted_SVM_tfidf = model_SVM_tfidf.predict(tfidf_vect.transform(X_test_test))
print(metrics.accuracy_score(y_test_test, predicted_SVM_tfidf))

0.438818565401


In [33]:
pipeline = Pipeline([
    ('tfidf', TfidfVectorizer(token_pattern='[\u4e00-\u9fff]+',ngram_range=(1, 2),max_df=0.75,analyzer='word',use_idf=True,norm='l2',min_df=0.005, max_features=None,stop_words=stop_ch1)),
    ('clf', LinearSVC(max_iter=100,penalty='l2'))
])
parameters = {
    'clf__C': [0.001, 0.01, 0.1, 1, 10, 100, 1000],
    'clf__loss': ('hinge','squared_hinge')
    
}

grid_search_tune = GridSearchCV(pipeline, parameters, cv=5, n_jobs=5, verbose=2)
grid_search_tune.fit(X_test_valid, y_test_valid)

print("Best parameters set:")
print(grid_search_tune.best_estimator_.steps)
print(grid_search_tune.best_score_)

Fitting 5 folds for each of 14 candidates, totalling 70 fits
[CV] clf__C=0.001, clf__loss=hinge ...................................
[CV] clf__C=0.001, clf__loss=hinge ...................................
[CV] clf__C=0.001, clf__loss=hinge ...................................
[CV] clf__C=0.001, clf__loss=hinge ...................................
[CV] clf__C=0.001, clf__loss=hinge ...................................
[CV] .................... clf__C=0.001, clf__loss=hinge, total=   0.2s
[CV] clf__C=0.001, clf__loss=squared_hinge ...........................
[CV] .................... clf__C=0.001, clf__loss=hinge, total=   0.2s
[CV] clf__C=0.001, clf__loss=squared_hinge ...........................
[CV] .................... clf__C=0.001, clf__loss=hinge, total=   0.2s
[CV] .................... clf__C=0.001, clf__loss=hinge, total=   0.2s
[CV] clf__C=0.001, clf__loss=squared_hinge ...........................
[CV] clf__C=0.001, clf__loss=squared_hinge ...........................
[CV] ...........

[Parallel(n_jobs=5)]: Done  31 tasks      | elapsed:    2.1s


[CV] ................ clf__C=1, clf__loss=squared_hinge, total=   0.2s
[CV] clf__C=10, clf__loss=hinge ......................................
[CV] ................ clf__C=1, clf__loss=squared_hinge, total=   0.2s
[CV] clf__C=10, clf__loss=hinge ......................................
[CV] ................ clf__C=1, clf__loss=squared_hinge, total=   0.2s
[CV] clf__C=10, clf__loss=hinge ......................................
[CV] ................ clf__C=1, clf__loss=squared_hinge, total=   0.2s
[CV] clf__C=10, clf__loss=hinge ......................................
[CV] ................ clf__C=1, clf__loss=squared_hinge, total=   0.2s
[CV] clf__C=10, clf__loss=hinge ......................................
[CV] ....................... clf__C=10, clf__loss=hinge, total=   0.3s
[CV] clf__C=10, clf__loss=squared_hinge ..............................
[CV] ....................... clf__C=10, clf__loss=hinge, total=   0.4s
[CV] clf__C=10, clf__loss=squared_hinge ..............................
[CV] .

[Parallel(n_jobs=5)]: Done  70 out of  70 | elapsed:    5.0s finished


In [34]:
pipeline = Pipeline([
    ('tfidf', TfidfVectorizer(token_pattern='[\u4e00-\u9fff]+',ngram_range=(1, 2),max_df=0.75,analyzer='word',use_idf=True,norm='l2',min_df=0.005, max_features=None,stop_words=stop_ch1)),
    ('clf', LinearSVC(max_iter=100,penalty='l2',loss='hinge'))
])
parameters = {
    'clf__C': [0.011,0.012,0.013,0.014,0.015,0.016,0.017,0.018,0.019]
}

grid_search_tune = GridSearchCV(pipeline, parameters, cv=5, n_jobs=5, verbose=2)
grid_search_tune.fit(X_test_valid, y_test_valid)

print("Best parameters set:")
print(grid_search_tune.best_estimator_.steps)
print(grid_search_tune.best_score_)

Fitting 5 folds for each of 9 candidates, totalling 45 fits
[CV] clf__C=0.011 ....................................................
[CV] clf__C=0.011 ....................................................
[CV] clf__C=0.011 ....................................................
[CV] clf__C=0.011 ....................................................
[CV] clf__C=0.011 ....................................................
[CV] ..................................... clf__C=0.011, total=   0.2s
[CV] clf__C=0.012 ....................................................
[CV] ..................................... clf__C=0.011, total=   0.2s
[CV] clf__C=0.012 ....................................................
[CV] ..................................... clf__C=0.011, total=   0.2s
[CV] clf__C=0.012 ....................................................
[CV] ..................................... clf__C=0.011, total=   0.2s
[CV] ..................................... clf__C=0.011, total=   0.2s
[CV] clf__C=0.012

[Parallel(n_jobs=5)]: Done  31 tasks      | elapsed:    2.1s


[CV] ..................................... clf__C=0.018, total=   0.2s
[CV] clf__C=0.019 ....................................................
[CV] ..................................... clf__C=0.018, total=   0.2s
[CV] clf__C=0.019 ....................................................
[CV] ..................................... clf__C=0.018, total=   0.2s
[CV] clf__C=0.019 ....................................................
[CV] ..................................... clf__C=0.018, total=   0.2s
[CV] clf__C=0.019 ....................................................
[CV] ..................................... clf__C=0.018, total=   0.2s
[CV] clf__C=0.019 ....................................................
[CV] ..................................... clf__C=0.019, total=   0.2s
[CV] ..................................... clf__C=0.019, total=   0.2s
[CV] ..................................... clf__C=0.019, total=   0.2s
[CV] ..................................... clf__C=0.019, total=   0.2s
[CV] .

[Parallel(n_jobs=5)]: Done  45 out of  45 | elapsed:    2.8s finished


Best parameters set:
[('tfidf', TfidfVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_features=None, min_df=0.005,
        ngram_range=(1, 2), norm='l2', preprocessor=None, smooth_idf=True,
        stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'],
        strip_accents=None, sublinear_tf=False,
        token_pattern='[一-\u9fff]+', tokenizer=None, use_idf=True,
        vocabulary=None)), ('clf', LinearSVC(C=0.014, class_weight=None, dual=True, fit_intercept=True,
     intercept_scaling=1, loss='hinge', max_iter=100, multi_class='ovr',
     penalty='l2', random_state=None, tol=0.0001, verbose=0))]
0.456842105263


C=0.01, 0.452631578947

C=0014, 0.456842105263

### Tf-idf + SGD

In [43]:
tfidf_vec = TfidfVectorizer(token_pattern='[\u4e00-\u9fff]+',ngram_range=(1, 2),max_df=0.75,analyzer='word',use_idf=True,norm='l2',min_df=0.005, max_features=None,stop_words=stop_ch1)
X_train_tfidf = tfidf_vect.fit_transform(X_train)

clf_SGD_tfidf = SGDClassifier()
model_SGD_tfidf = clf_SGD_tfidf.fit(X_train_tfidf, y_train)
predicted_SGD_tfidf = model_SGD_tfidf.predict(tfidf_vect.transform(X_test_test))
print(metrics.accuracy_score(y_test_test, predicted_SGD_tfidf))

0.455696202532


/Users/manyingz/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/stochastic_gradient.py:128: FutureWarning: max_iter and tol parameters have been added in <class 'sklearn.linear_model.stochastic_gradient.SGDClassifier'> in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  "and default tol will be 1e-3." % type(self), FutureWarning)


In [40]:
pipeline = Pipeline([
    ('tfidf', TfidfVectorizer(token_pattern='[\u4e00-\u9fff]+',ngram_range=(1, 2),max_df=0.75,analyzer='word',use_idf=True,norm='l2',min_df=0.005, max_features=None,stop_words=stop_ch1)),
    ('clf', SGDClassifier(max_iter=100,penalty='l2'))
])
parameters = {
    'clf__loss': ('hinge', 'log', 'modified_huber','perceptron','squared_loss','huber','epsilon_insensitive'),
    'clf__alpha':[0.0001,0.001,0.01,0.02]
    
}

grid_search_tune = GridSearchCV(pipeline, parameters, cv=5, n_jobs=5, verbose=2)
grid_search_tune.fit(X_test_valid, y_test_valid)

print("Best parameters set:")
print(grid_search_tune.best_estimator_.steps)
print(grid_search_tune.best_score_)

Fitting 5 folds for each of 28 candidates, totalling 140 fits
[CV] clf__alpha=0.0001, clf__loss=hinge ..............................
[CV] clf__alpha=0.0001, clf__loss=hinge ..............................
[CV] clf__alpha=0.0001, clf__loss=hinge ..............................
[CV] clf__alpha=0.0001, clf__loss=hinge ..............................
[CV] clf__alpha=0.0001, clf__loss=hinge ..............................
[CV] ............... clf__alpha=0.0001, clf__loss=hinge, total=   0.3s
[CV] clf__alpha=0.0001, clf__loss=log ................................
[CV] ............... clf__alpha=0.0001, clf__loss=hinge, total=   0.3s
[CV] clf__alpha=0.0001, clf__loss=log ................................
[CV] ............... clf__alpha=0.0001, clf__loss=hinge, total=   0.3s
[CV] ............... clf__alpha=0.0001, clf__loss=hinge, total=   0.4s
[CV] clf__alpha=0.0001, clf__loss=log ................................
[CV] clf__alpha=0.0001, clf__loss=log ................................
[CV] ..........

[Parallel(n_jobs=5)]: Done  31 tasks      | elapsed:    2.9s


[CV] clf__alpha=0.001, clf__loss=hinge ...............................
[CV] . clf__alpha=0.0001, clf__loss=epsilon_insensitive, total=   0.3s
[CV] clf__alpha=0.001, clf__loss=hinge ...............................
[CV] ................ clf__alpha=0.001, clf__loss=hinge, total=   0.3s
[CV] clf__alpha=0.001, clf__loss=log .................................
[CV] ................ clf__alpha=0.001, clf__loss=hinge, total=   0.3s
[CV] clf__alpha=0.001, clf__loss=log .................................
[CV] ................ clf__alpha=0.001, clf__loss=hinge, total=   0.3s
[CV] clf__alpha=0.001, clf__loss=log .................................
[CV] ................ clf__alpha=0.001, clf__loss=hinge, total=   0.3s
[CV] clf__alpha=0.001, clf__loss=log .................................
[CV] ................ clf__alpha=0.001, clf__loss=hinge, total=   0.3s
[CV] clf__alpha=0.001, clf__loss=log .................................
[CV] .................. clf__alpha=0.001, clf__loss=log, total=   0.4s
[CV] c

[CV] clf__alpha=0.01, clf__loss=huber ................................
[CV] .......... clf__alpha=0.01, clf__loss=squared_loss, total=   0.3s
[CV] .......... clf__alpha=0.01, clf__loss=squared_loss, total=   0.3s
[CV] clf__alpha=0.01, clf__loss=huber ................................
[CV] clf__alpha=0.01, clf__loss=huber ................................
[CV] .......... clf__alpha=0.01, clf__loss=squared_loss, total=   0.3s
[CV] clf__alpha=0.01, clf__loss=huber ................................
[CV] ................. clf__alpha=0.01, clf__loss=huber, total=   0.3s
[CV] clf__alpha=0.01, clf__loss=epsilon_insensitive ..................
[CV] ................. clf__alpha=0.01, clf__loss=huber, total=   0.3s
[CV] clf__alpha=0.01, clf__loss=epsilon_insensitive ..................
[CV] ................. clf__alpha=0.01, clf__loss=huber, total=   0.3s
[CV] clf__alpha=0.01, clf__loss=epsilon_insensitive ..................
[CV] ................. clf__alpha=0.01, clf__loss=huber, total=   0.3s
[CV] c

[Parallel(n_jobs=5)]: Done 140 out of 140 | elapsed:   12.0s finished


Best parameters set:
[('tfidf', TfidfVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_features=None, min_df=0.005,
        ngram_range=(1, 2), norm='l2', preprocessor=None, smooth_idf=True,
        stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'],
        strip_accents=None, sublinear_tf=False,
        token_pattern='[一-\u9fff]+', tokenizer=None, use_idf=True,
        vocabulary=None)), ('clf', SGDClassifier(alpha=0.01, average=False, class_weight=None, epsilon=0.1,
       eta0=0.0, fit_intercept=True, l1_ratio=0.15,
       learning_rate='optimal', loss='modified_huber', max_iter=100,
       n_iter=None, n_jobs=1, penalty='l2', power_t=0.5, random_state=None,
       shuffle=True, tol=None, verbose=0, warm_start=False))]
0.461052631579


In [41]:
pipeline = Pipeline([
    ('tfidf', TfidfVectorizer(token_pattern='[\u4e00-\u9fff]+',ngram_range=(1, 2),max_df=0.75,analyzer='word',use_idf=True,norm='l2',min_df=0.005, max_features=None,stop_words=stop_ch1)),
    ('clf', SGDClassifier(max_iter=100,penalty='l2'))
])
parameters = {
    'clf__loss': ('hinge', 'log', 'modified_huber'),
    'clf__alpha':[0.002,0.003,0.004,0.005,0.006,0.007,0.008,0.009,0.01,0.011,0.012,0.013,0.014,0.015,0.016,0.017,0.018,0.019]
    
}

grid_search_tune = GridSearchCV(pipeline, parameters, cv=5, n_jobs=5, verbose=2)
grid_search_tune.fit(X_test_valid, y_test_valid)

print("Best parameters set:")
print(grid_search_tune.best_estimator_.steps)
print(grid_search_tune.best_score_)

Fitting 5 folds for each of 54 candidates, totalling 270 fits
[CV] clf__alpha=0.002, clf__loss=hinge ...............................
[CV] clf__alpha=0.002, clf__loss=hinge ...............................
[CV] clf__alpha=0.002, clf__loss=hinge ...............................
[CV] clf__alpha=0.002, clf__loss=hinge ...............................
[CV] clf__alpha=0.002, clf__loss=hinge ...............................
[CV] ................ clf__alpha=0.002, clf__loss=hinge, total=   0.2s
[CV] clf__alpha=0.002, clf__loss=log .................................
[CV] ................ clf__alpha=0.002, clf__loss=hinge, total=   0.2s
[CV] ................ clf__alpha=0.002, clf__loss=hinge, total=   0.2s
[CV] clf__alpha=0.002, clf__loss=log .................................
[CV] clf__alpha=0.002, clf__loss=log .................................
[CV] ................ clf__alpha=0.002, clf__loss=hinge, total=   0.2s
[CV] clf__alpha=0.002, clf__loss=log .................................
[CV] ..........

[Parallel(n_jobs=5)]: Done  31 tasks      | elapsed:    3.0s


[CV] .................. clf__alpha=0.004, clf__loss=log, total=   0.4s
[CV] clf__alpha=0.004, clf__loss=modified_huber ......................
[CV] .................. clf__alpha=0.004, clf__loss=log, total=   0.4s
[CV] clf__alpha=0.004, clf__loss=modified_huber ......................
[CV] .................. clf__alpha=0.004, clf__loss=log, total=   0.4s
[CV] clf__alpha=0.004, clf__loss=modified_huber ......................
[CV] .................. clf__alpha=0.004, clf__loss=log, total=   0.4s
[CV] clf__alpha=0.004, clf__loss=modified_huber ......................
[CV] .................. clf__alpha=0.004, clf__loss=log, total=   0.4s
[CV] clf__alpha=0.004, clf__loss=modified_huber ......................
[CV] ....... clf__alpha=0.004, clf__loss=modified_huber, total=   0.3s
[CV] clf__alpha=0.005, clf__loss=hinge ...............................
[CV] ....... clf__alpha=0.004, clf__loss=modified_huber, total=   0.3s
[CV] clf__alpha=0.005, clf__loss=hinge ...............................
[CV] .

[CV] ................ clf__alpha=0.008, clf__loss=hinge, total=   0.3s
[CV] clf__alpha=0.008, clf__loss=log .................................
[CV] ................ clf__alpha=0.008, clf__loss=hinge, total=   0.3s
[CV] clf__alpha=0.008, clf__loss=log .................................
[CV] .................. clf__alpha=0.008, clf__loss=log, total=   0.4s
[CV] .................. clf__alpha=0.008, clf__loss=log, total=   0.4s
[CV] clf__alpha=0.008, clf__loss=modified_huber ......................
[CV] clf__alpha=0.008, clf__loss=modified_huber ......................
[CV] .................. clf__alpha=0.008, clf__loss=log, total=   0.4s
[CV] .................. clf__alpha=0.008, clf__loss=log, total=   0.4s
[CV] clf__alpha=0.008, clf__loss=modified_huber ......................
[CV] clf__alpha=0.008, clf__loss=modified_huber ......................
[CV] .................. clf__alpha=0.008, clf__loss=log, total=   0.4s
[CV] clf__alpha=0.008, clf__loss=modified_huber ......................
[CV] .

[CV] ................ clf__alpha=0.012, clf__loss=hinge, total=   0.3s
[CV] clf__alpha=0.012, clf__loss=log .................................
[CV] ................ clf__alpha=0.012, clf__loss=hinge, total=   0.2s
[CV] ................ clf__alpha=0.012, clf__loss=hinge, total=   0.3s
[CV] clf__alpha=0.012, clf__loss=log .................................
[CV] clf__alpha=0.012, clf__loss=log .................................


[Parallel(n_jobs=5)]: Done 152 tasks      | elapsed:   13.4s


[CV] ................ clf__alpha=0.012, clf__loss=hinge, total=   0.3s
[CV] clf__alpha=0.012, clf__loss=log .................................
[CV] .................. clf__alpha=0.012, clf__loss=log, total=   0.4s
[CV] clf__alpha=0.012, clf__loss=modified_huber ......................
[CV] .................. clf__alpha=0.012, clf__loss=log, total=   0.4s
[CV] clf__alpha=0.012, clf__loss=modified_huber ......................
[CV] .................. clf__alpha=0.012, clf__loss=log, total=   0.3s
[CV] .................. clf__alpha=0.012, clf__loss=log, total=   0.3s
[CV] clf__alpha=0.012, clf__loss=modified_huber ......................
[CV] clf__alpha=0.012, clf__loss=modified_huber ......................
[CV] .................. clf__alpha=0.012, clf__loss=log, total=   0.4s
[CV] clf__alpha=0.012, clf__loss=modified_huber ......................
[CV] ....... clf__alpha=0.012, clf__loss=modified_huber, total=   0.3s
[CV] clf__alpha=0.013, clf__loss=hinge ...............................
[CV] .

[CV] clf__alpha=0.016, clf__loss=log .................................
[CV] clf__alpha=0.016, clf__loss=log .................................
[CV] ................ clf__alpha=0.016, clf__loss=hinge, total=   0.3s
[CV] clf__alpha=0.016, clf__loss=log .................................
[CV] ................ clf__alpha=0.016, clf__loss=hinge, total=   0.3s
[CV] clf__alpha=0.016, clf__loss=log .................................
[CV] .................. clf__alpha=0.016, clf__loss=log, total=   0.4s
[CV] clf__alpha=0.016, clf__loss=modified_huber ......................
[CV] .................. clf__alpha=0.016, clf__loss=log, total=   0.4s
[CV] clf__alpha=0.016, clf__loss=modified_huber ......................
[CV] .................. clf__alpha=0.016, clf__loss=log, total=   0.4s
[CV] clf__alpha=0.016, clf__loss=modified_huber ......................
[CV] .................. clf__alpha=0.016, clf__loss=log, total=   0.3s
[CV] clf__alpha=0.016, clf__loss=modified_huber ......................
[CV] .

[Parallel(n_jobs=5)]: Done 270 out of 270 | elapsed:   24.9s finished


Best parameters set:
[('tfidf', TfidfVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=0.75, max_features=None, min_df=0.005,
        ngram_range=(1, 2), norm='l2', preprocessor=None, smooth_idf=True,
        stop_words=['的', '了', '和', '而', '且', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '一个', '一', '二', '三', '四', '五', '六', '七', '八', '九', '十', '十一', '十二'],
        strip_accents=None, sublinear_tf=False,
        token_pattern='[一-\u9fff]+', tokenizer=None, use_idf=True,
        vocabulary=None)), ('clf', SGDClassifier(alpha=0.012, average=False, class_weight=None, epsilon=0.1,
       eta0=0.0, fit_intercept=True, l1_ratio=0.15,
       learning_rate='optimal', loss='modified_huber', max_iter=100,
       n_iter=None, n_jobs=1, penalty='l2', power_t=0.5, random_state=None,
       shuffle=True, tol=None, verbose=0, warm_start=False))]
0.465263157895


loss='modified_huber', alpha=0.01, 0.461052631579

loss='modified_huber', alpha=0.012, 0.465263157895

### ugly hack word2vec to sklearn ... coming soon

In [ ]:
http://nadbordrozd.github.io/blog/2016/05/20/text-classification-with-word2vec/